In [1]:
# Import libraries
import pandas as pd
import numpy as np

In [2]:
# Import data
dataset = pd.read_csv('data/Churn_Modelling.csv')
X = dataset.iloc[:, 3:13]
y = dataset.iloc[:, 13]

In [3]:
# Encode categorical data and scale continuous data
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import make_column_transformer
preprocess = make_column_transformer(
        (OneHotEncoder(), ['Geography', 'Gender']),
        (StandardScaler(), ['CreditScore', 'Age', 'Tenure', 'Balance',
                            'NumOfProducts', 'HasCrCard', 'IsActiveMember', 
                            'EstimatedSalary']))
X = preprocess.fit_transform(X)
X = np.delete(X, [0,3], 1)

In [4]:
# Split in train/test
y = y.values
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 0)

## Partie 2 - ANN

In [5]:
# Importing the Keras libraries and packages
from keras.models import Sequential
from keras.layers import Dense

Using TensorFlow backend.


In [6]:
# Initialising the ANN
classifier = Sequential()

# Adding the input layer and the first hidden layer
classifier.add(Dense(units = 6, kernel_initializer = 'uniform', activation = 'relu', input_dim = 11))

# Adding the second hidden layer
classifier.add(Dense(units = 6, kernel_initializer = 'uniform', activation = 'relu'))

# Adding the output layer
classifier.add(Dense(units = 1, kernel_initializer = 'uniform', activation = 'sigmoid'))

# Compiling the ANN
classifier.compile(optimizer = 'adam', loss = 'binary_crossentropy', metrics = ['accuracy'])

# Fitting the ANN to the Training set
classifier.fit(X_train, y_train, batch_size = 10, epochs = 100)

Epoch 1/100
8000/8000 [==============================] - 12s 1ms/step - loss: 0.4945 - accuracy: 0.7956
Epoch 2/100
8000/8000 [==============================] - 4s 454us/step - loss: 0.4332 - accuracy: 0.7960
Epoch 3/100
8000/8000 [==============================] - 3s 430us/step - loss: 0.4282 - accuracy: 0.7960
Epoch 4/100
8000/8000 [==============================] - 4s 460us/step - loss: 0.4231 - accuracy: 0.7965
Epoch 5/100
8000/8000 [==============================] - 4s 440us/step - loss: 0.4186 - accuracy: 0.8221
Epoch 6/100
8000/8000 [==============================] - 3s 428us/step - loss: 0.4165 - accuracy: 0.8273
Epoch 7/100
8000/8000 [==============================] - 3s 425us/step - loss: 0.4146 - accuracy: 0.8288
Epoch 8/100
8000/8000 [==============================] - 4s 459us/step - loss: 0.4133 - accuracy: 0.8301
Epoch 9/100
8000/8000 [==============================] - 10s 1ms/step - loss: 0.4120 - accuracy: 0.8320
Epoch 10/100
8000/8000 [==============================] -

8000/8000 [==============================] - 4s 475us/step - loss: 0.4004 - accuracy: 0.8355
Epoch 79/100
8000/8000 [==============================] - 4s 533us/step - loss: 0.4002 - accuracy: 0.8357
Epoch 80/100
8000/8000 [==============================] - 4s 507us/step - loss: 0.4000 - accuracy: 0.8351
Epoch 81/100
8000/8000 [==============================] - 6s 689us/step - loss: 0.4005 - accuracy: 0.8350
Epoch 82/100
8000/8000 [==============================] - 8s 946us/step - loss: 0.4000 - accuracy: 0.8347
Epoch 83/100
8000/8000 [==============================] - 5s 605us/step - loss: 0.4005 - accuracy: 0.8351
Epoch 84/100
8000/8000 [==============================] - 9s 1ms/step - loss: 0.4000 - accuracy: 0.8344
Epoch 85/100
8000/8000 [==============================] - 28s 4ms/step - loss: 0.4002 - accuracy: 0.8359
Epoch 86/100
8000/8000 [==============================] - 21s 3ms/step - loss: 0.4003 - accuracy: 0.8342
Epoch 87/100
8000/8000 [==============================] - 21s 3

## Partie 3 - Prédictions et Évaluation

In [7]:
# Predicting the Test set results
y_pred = classifier.predict(X_test)
y_pred = (y_pred > 0.5)

In [8]:
# Predicting a single new observation
"""Predict if the customer with the following informations will leave the bank:
Geography: France
Credit Score: 600
Gender: Male
Age: 40
Tenure: 3
Balance: 60000
Number of Products: 2
Has Credit Card: Yes
Is Active Member: Yes
Estimated Salary: 50000"""
Xnew = pd.DataFrame(data={
        'CreditScore': [600], 
        'Geography': ['France'], 
        'Gender': ['Male'],
        'Age': [40],
        'Tenure': [3],
        'Balance': [60000],
        'NumOfProducts': [2],
        'HasCrCard': [1],
        'IsActiveMember': [1],
        'EstimatedSalary': [50000]})
Xnew = preprocess.transform(Xnew)
Xnew = np.delete(Xnew, [0,3], 1)
new_prediction = classifier.predict(Xnew)
new_prediction = (new_prediction > 0.5)

In [9]:
# Making the Confusion Matrix
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test, y_pred)

In [10]:
print(cm)

[[1538   57]
 [ 262  143]]


In [11]:
# Evaluate
def build_classifier(optimizer='adam'):
    classifier = Sequential()
    classifier.add(Dense(units = 6, kernel_initializer = 'uniform', activation = 'relu', input_dim = 11))
    classifier.add(Dense(units = 6, kernel_initializer = 'uniform', activation = 'relu'))
    classifier.add(Dense(units = 1, kernel_initializer = 'uniform', activation = 'sigmoid'))
    classifier.compile(optimizer = optimizer, loss = 'binary_crossentropy', metrics = ['accuracy'])
    return classifier

In [12]:
# Evaluate
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score
classifier = KerasClassifier(build_fn = build_classifier, batch_size = 10, epochs = 100)
accuracies = cross_val_score(estimator = classifier, X = X_train, y = y_train, 
                             cv = 10, n_jobs = -1)
mean = accuracies.mean()
variance = accuracies.std()

In [13]:
print(mean)

0.839125007390976


In [14]:
print(variance)

0.013636458449890651


In [15]:
# Tune
from sklearn.model_selection import GridSearchCV
classifier = KerasClassifier(build_fn = build_classifier)
parameters = {'batch_size': [25, 32],
              'epochs': [100, 500],
              'optimizer': ['adam', 'rmsprop']}
grid_search = GridSearchCV(estimator = classifier,
                           param_grid = parameters,
                           scoring = 'accuracy',
                           cv = 10)
grid_search = grid_search.fit(X_train, y_train)
best_parameters = grid_search.best_params_
best_accuracy = grid_search.best_score_

Epoch 1/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.5319 - accuracy: 0.7971
Epoch 2/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4374 - accuracy: 0.7971
Epoch 3/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4306 - accuracy: 0.7971
Epoch 4/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.4267 - accuracy: 0.7971
Epoch 5/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4229 - accuracy: 0.7971
Epoch 6/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4196 - accuracy: 0.8090
Epoch 7/100
7200/7200 [==============================] - 17s 2ms/step - loss: 0.4172 - accuracy: 0.8224
Epoch 8/100
7200/7200 [==============================] - 17s 2ms/step - loss: 0.4167 - accuracy: 0.8253
Epoch 9/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4151 - accuracy: 0.8267
Epoch 10/100
7200/7200 [==============================] - 16s 2m

7200/7200 [==============================] - 15s 2ms/step - loss: 0.4005 - accuracy: 0.8333
Epoch 80/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4001 - accuracy: 0.8339
Epoch 81/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.3997 - accuracy: 0.8332
Epoch 82/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.3999 - accuracy: 0.8351
Epoch 83/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4003 - accuracy: 0.8335
Epoch 84/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.4000 - accuracy: 0.8339
Epoch 85/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.3997 - accuracy: 0.8347
Epoch 86/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4000 - accuracy: 0.8343
Epoch 87/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.3999 - accuracy: 0.8347
Epoch 88/100
7200/7200 [==============================] - 13s 2ms/st

7200/7200 [==============================] - 13s 2ms/step - loss: 0.3930 - accuracy: 0.8376
Epoch 58/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.3928 - accuracy: 0.8375
Epoch 59/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.3928 - accuracy: 0.8369
Epoch 60/100
7200/7200 [==============================] - 8s 1ms/step - loss: 0.3929 - accuracy: 0.8364
Epoch 61/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.3922 - accuracy: 0.8378
Epoch 62/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.3920 - accuracy: 0.8382
Epoch 63/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.3924 - accuracy: 0.8386
Epoch 64/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.3926 - accuracy: 0.8388
Epoch 65/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.3919 - accuracy: 0.8383
Epoch 66/100
7200/7200 [==============================] - 15s 2ms/ste

7200/7200 [==============================] - 14s 2ms/step - loss: 0.4045 - accuracy: 0.8358
Epoch 35/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4048 - accuracy: 0.8353
Epoch 36/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4047 - accuracy: 0.8349
Epoch 37/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4043 - accuracy: 0.8361
Epoch 38/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4040 - accuracy: 0.8356
Epoch 39/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.4039 - accuracy: 0.8358
Epoch 40/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.4041 - accuracy: 0.8344
Epoch 41/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.4038 - accuracy: 0.8347
Epoch 42/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4036 - accuracy: 0.8353
Epoch 43/100
7200/7200 [==============================] - 14s 2ms/st

7200/7200 [==============================] - 15s 2ms/step - loss: 0.4113 - accuracy: 0.8314
Epoch 13/100
7200/7200 [==============================] - 13s 2ms/step - loss: 0.4108 - accuracy: 0.8318
Epoch 14/100
7200/7200 [==============================] - 15s 2ms/step - loss: 0.4097 - accuracy: 0.8326
Epoch 15/100
7200/7200 [==============================] - 13s 2ms/step - loss: 0.4089 - accuracy: 0.8329
Epoch 16/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.4086 - accuracy: 0.8343
Epoch 17/100
7200/7200 [==============================] - 11s 2ms/step - loss: 0.4080 - accuracy: 0.8338
Epoch 18/100
7200/7200 [==============================] - 14s 2ms/step - loss: 0.4072 - accuracy: 0.8344
Epoch 19/100
7200/7200 [==============================] - 16s 2ms/step - loss: 0.4066 - accuracy: 0.8356
Epoch 20/100
7200/7200 [==============================] - 9s 1ms/step - loss: 0.4061 - accuracy: 0.8357
Epoch 21/100
7200/7200 [==============================] - 14s 2ms/ste

...

8000/8000 [==============================] - 1s 119us/step - loss: 0.3995 - accuracy: 0.8344
Epoch 185/500
8000/8000 [==============================] - 1s 125us/step - loss: 0.3989 - accuracy: 0.8359
Epoch 186/500
8000/8000 [==============================] - 1s 114us/step - loss: 0.3988 - accuracy: 0.8355
Epoch 187/500
8000/8000 [==============================] - 1s 94us/step - loss: 0.3996 - accuracy: 0.8357
Epoch 188/500
8000/8000 [==============================] - 1s 113us/step - loss: 0.3985 - accuracy: 0.8344
Epoch 189/500
8000/8000 [==============================] - 1s 118us/step - loss: 0.3991 - accuracy: 0.8350
Epoch 190/500
8000/8000 [==============================] - 1s 91us/step - loss: 0.3989 - accuracy: 0.8369
Epoch 191/500
8000/8000 [==============================] - 1s 108us/step - loss: 0.3992 - accuracy: 0.8340
Epoch 192/500
8000/8000 [==============================] - 1s 136us/step - loss: 0.3990 - accuracy: 0.8342
Epoch 193/500
8000/8000 [============================

8000/8000 [==============================] - 1s 96us/step - loss: 0.3991 - accuracy: 0.8361
Epoch 261/500
8000/8000 [==============================] - 1s 87us/step - loss: 0.3990 - accuracy: 0.8354
Epoch 262/500
8000/8000 [==============================] - 1s 101us/step - loss: 0.3987 - accuracy: 0.8347
Epoch 263/500
8000/8000 [==============================] - 1s 124us/step - loss: 0.3991 - accuracy: 0.8344
Epoch 264/500
8000/8000 [==============================] - 1s 122us/step - loss: 0.3990 - accuracy: 0.8361
Epoch 265/500
8000/8000 [==============================] - 1s 122us/step - loss: 0.3989 - accuracy: 0.8350
Epoch 266/500
8000/8000 [==============================] - 1s 129us/step - loss: 0.3992 - accuracy: 0.8345
Epoch 267/500
8000/8000 [==============================] - 1s 121us/step - loss: 0.3988 - accuracy: 0.8364
Epoch 268/500
8000/8000 [==============================] - 1s 115us/step - loss: 0.3989 - accuracy: 0.8351
Epoch 269/500
8000/8000 [============================

8000/8000 [==============================] - 1s 137us/step - loss: 0.3965 - accuracy: 0.8351
Epoch 337/500
8000/8000 [==============================] - 1s 135us/step - loss: 0.3963 - accuracy: 0.8347
Epoch 338/500
8000/8000 [==============================] - 1s 130us/step - loss: 0.3960 - accuracy: 0.8357
Epoch 339/500
8000/8000 [==============================] - 1s 126us/step - loss: 0.3962 - accuracy: 0.8353
Epoch 340/500
8000/8000 [==============================] - 1s 127us/step - loss: 0.3955 - accuracy: 0.8364
Epoch 341/500
8000/8000 [==============================] - 1s 112us/step - loss: 0.3955 - accuracy: 0.8359
Epoch 342/500
8000/8000 [==============================] - 1s 149us/step - loss: 0.3954 - accuracy: 0.8357
Epoch 343/500
8000/8000 [==============================] - 1s 140us/step - loss: 0.3952 - accuracy: 0.8361
Epoch 344/500
8000/8000 [==============================] - 1s 111us/step - loss: 0.3951 - accuracy: 0.8360
Epoch 345/500
8000/8000 [==========================

8000/8000 [==============================] - 1s 120us/step - loss: 0.3927 - accuracy: 0.8371
Epoch 413/500
8000/8000 [==============================] - 1s 118us/step - loss: 0.3928 - accuracy: 0.8375
Epoch 414/500
8000/8000 [==============================] - 1s 124us/step - loss: 0.3930 - accuracy: 0.8355
Epoch 415/500
8000/8000 [==============================] - 1s 93us/step - loss: 0.3930 - accuracy: 0.8357
Epoch 416/500
8000/8000 [==============================] - 1s 112us/step - loss: 0.3929 - accuracy: 0.8366
Epoch 417/500
8000/8000 [==============================] - 1s 139us/step - loss: 0.3933 - accuracy: 0.8345
Epoch 418/500
8000/8000 [==============================] - 1s 113us/step - loss: 0.3931 - accuracy: 0.8354
Epoch 419/500
8000/8000 [==============================] - 1s 102us/step - loss: 0.3922 - accuracy: 0.8372
Epoch 420/500
8000/8000 [==============================] - 1s 118us/step - loss: 0.3930 - accuracy: 0.8366
Epoch 421/500
8000/8000 [===========================

8000/8000 [==============================] - 1s 114us/step - loss: 0.3920 - accuracy: 0.8359
Epoch 489/500
8000/8000 [==============================] - 1s 100us/step - loss: 0.3921 - accuracy: 0.8342
Epoch 490/500
8000/8000 [==============================] - 1s 105us/step - loss: 0.3924 - accuracy: 0.8349
Epoch 491/500
8000/8000 [==============================] - 1s 110us/step - loss: 0.3921 - accuracy: 0.8353
Epoch 492/500
8000/8000 [==============================] - 1s 125us/step - loss: 0.3923 - accuracy: 0.8356
Epoch 493/500
8000/8000 [==============================] - 1s 131us/step - loss: 0.3919 - accuracy: 0.8357
Epoch 494/500
8000/8000 [==============================] - 1s 105us/step - loss: 0.3922 - accuracy: 0.8356
Epoch 495/500
8000/8000 [==============================] - 1s 123us/step - loss: 0.3923 - accuracy: 0.8356
Epoch 496/500
8000/8000 [==============================] - 1s 113us/step - loss: 0.3923 - accuracy: 0.8347
Epoch 497/500
8000/8000 [==========================

In [16]:
print(best_parameters)

{'batch_size': 25, 'epochs': 500, 'optimizer': 'adam'}
